<a href="https://colab.research.google.com/github/Lingeswaran2018/My_projects/blob/main/fine_tune_whisper_Sinhala.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Fine-Tune Whisper For Sinhala Voice to text transcription


## Prepare Environment

In [ ]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Tue Jan  7 17:50:11 2025       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla T4                       Off | 00000000:00:04.0 Off |                    0 |
| N/A   49C    P8               9W /  70W |      0MiB / 15360MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [ ]:
!pip install --upgrade --quiet pip
!pip install --upgrade --quiet datasets[audio] transformers accelerate evaluate jiwer tensorboard gradio

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 72.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.5/5.5 MB 140.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.5/57.5 MB 157.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 115.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.3/11.3 MB 168.2 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.
tensorflow 2.17.1 requires tensorboard<2.18,>=2.17, but you have tensorboard 2.18.0 which is incompatible.


In [ ]:
from huggingface_hub import notebook_login

notebook_login()

## Load Dataset

In [ ]:
!pip install huggingface-hub datasets git-lfs


In [ ]:
!pip install datasets
from datasets import load_dataset

common_voice = load_dataset("Lingalingeswaran/asr-sinhala-dataset_v3")


In [ ]:
print(common_voice['train'][0])  # Print the first sample of the training data


{'FileID': '0000f47c22', 'Speaker': '7ab05', 'Transcription': 'මහවැලි ගඟට ගොස් ආපසු එන ගමනේදී', 'AudioPath': './asr_sinhala/asr_sinhala/data/00/0000f47c22.flac', 'AudioData': [0.000762939453125, 0.00152587890625, 0.00115966796875, 0.0003662109375, 0.00115966796875, 0.0, -0.000396728515625, -0.000396728515625, 0.0003662109375, 0.000732421875, 0.0, 0.00152587890625, 0.000762939453125, 0.000762939453125, 0.00152587890625, 0.00152587890625, 0.000762939453125, 0.000396728515625, -3.0517578125e-05, -0.000762939453125, 0.000762939453125, 0.0003662109375, 0.0003662109375, 0.0, 0.0, -0.00042724609375, -0.0003662109375, 0.000732421875, -0.0003662109375, 0.000732421875, -0.000396728515625, -0.00042724609375, -0.000396728515625, -0.00079345703125, 0.000335693359375, 0.000396728515625, 0.001861572265625, 0.001220703125, 0.00030517578125, 0.001220703125, 0.001861572265625, 0.001220703125, 0.00146484375, 0.001190185546875, 0.00146484375, 0.00274658203125, 0.0010986328125, 0.00079345703125, 0.00149536

In [ ]:

print(common_voice)

DatasetDict({
    train: Dataset({
        features: ['FileID', 'Speaker', 'Transcription', 'AudioPath', 'AudioData', '__index_level_0__'],
        num_rows: 11357
    })
})


In [ ]:
common_voice = common_voice.remove_columns(["FileID", "Speaker","__index_level_0__"])

print(common_voice)

DatasetDict({
    train: Dataset({
        features: ['Transcription', 'AudioPath', 'AudioData'],
        num_rows: 11357
    })
})


In [ ]:

print(common_voice)

DatasetDict({
    train: Dataset({
        features: ['Transcription', 'AudioData'],
        num_rows: 11357
    })
})


## Prepare Feature Extractor, Tokenizer and Data

### Load WhisperFeatureExtractor

In [ ]:
from transformers import WhisperFeatureExtractor

feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-small")

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

preprocessor_config.json:   0%|          | 0.00/185k [00:00<?, ?B/s]

### Load WhisperTokenizer

In [ ]:
from transformers import WhisperTokenizer

tokenizer = WhisperTokenizer.from_pretrained("openai/whisper-small", language="Sinhala", task="transcribe")

tokenizer_config.json:   0%|          | 0.00/283k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/836k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.48M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/494k [00:00<?, ?B/s]

normalizer.json:   0%|          | 0.00/52.7k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/34.6k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.19k [00:00<?, ?B/s]

### Combine To Create A WhisperProcessor

In [ ]:
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained("openai/whisper-small", language="Sinhala", task="transcribe")

### Prepare Data

In [ ]:
print(common_voice["train"][0])

{'Transcription': 'මහවැලි ගඟට ගොස් ආපසු එන ගමනේදී', 'AudioData': [0.000762939453125, 0.00152587890625, 0.00115966796875, 0.0003662109375, 0.00115966796875, 0.0, -0.000396728515625, -0.000396728515625, 0.0003662109375, 0.000732421875, 0.0, 0.00152587890625, 0.000762939453125, 0.000762939453125, 0.00152587890625, 0.00152587890625, 0.000762939453125, 0.000396728515625, -3.0517578125e-05, -0.000762939453125, 0.000762939453125, 0.0003662109375, 0.0003662109375, 0.0, 0.0, -0.00042724609375, -0.0003662109375, 0.000732421875, -0.0003662109375, 0.000732421875, -0.000396728515625, -0.00042724609375, -0.000396728515625, -0.00079345703125, 0.000335693359375, 0.000396728515625, 0.001861572265625, 0.001220703125, 0.00030517578125, 0.001220703125, 0.001861572265625, 0.001220703125, 0.00146484375, 0.001190185546875, 0.00146484375, 0.00274658203125, 0.0010986328125, 0.00079345703125, 0.001495361328125, 0.00079345703125, 0.001129150390625, 0.000396728515625, -0.00042724609375, 3.0517578125e-05, 0.000732

In [ ]:
from datasets import Audio

common_voice = common_voice.cast_column("AudioData", Audio(sampling_rate=16000))

TypeError: Couldn't cast array of type list<item: float> to struct<bytes: binary, path: string>

In [ ]:
import soundfile as sf

def prepare_dataset(batch):
    # load audio data
    audio = batch["audio"]

    # resample to 16kHz
    # Assuming audio["array"] is the raw audio data
    batch["audio"]["array"], batch["audio"]["sampling_rate"] = sf.read(audio["AudioPath"])  # Read audio file
    batch["audio"]["array"] = sf.resample(batch["audio"]["array"], audio["sampling_rate"], 16000)  # Resample audio
    batch["audio"]["sampling_rate"] = 16000

    # compute log-Mel input features
    batch["input_features"] = feature_extractor(batch["audio"]["array"], sampling_rate=batch["audio"]["sampling_rate"]).input_features[0]

    # encode target text to label ids
    batch["labels"] = tokenizer(batch["sentence"]).input_ids
    return batch

In [ ]:
from datasets import Audio

common_voice = common_voice.cast_column("audio", Audio(sampling_rate=16000))

In [ ]:
print(common_voice["train"][0])

{'Transcription': 'මහවැලි ගඟට ගොස් ආපසු එන ගමනේදී', 'AudioPath': './asr_sinhala/asr_sinhala/data/00/0000f47c22.flac', 'AudioData': [0.000762939453125, 0.00152587890625, 0.00115966796875, 0.0003662109375, 0.00115966796875, 0.0, -0.000396728515625, -0.000396728515625, 0.0003662109375, 0.000732421875, 0.0, 0.00152587890625, 0.000762939453125, 0.000762939453125, 0.00152587890625, 0.00152587890625, 0.000762939453125, 0.000396728515625, -3.0517578125e-05, -0.000762939453125, 0.000762939453125, 0.0003662109375, 0.0003662109375, 0.0, 0.0, -0.00042724609375, -0.0003662109375, 0.000732421875, -0.0003662109375, 0.000732421875, -0.000396728515625, -0.00042724609375, -0.000396728515625, -0.00079345703125, 0.000335693359375, 0.000396728515625, 0.001861572265625, 0.001220703125, 0.00030517578125, 0.001220703125, 0.001861572265625, 0.001220703125, 0.00146484375, 0.001190185546875, 0.00146484375, 0.00274658203125, 0.0010986328125, 0.00079345703125, 0.001495361328125, 0.00079345703125, 0.001129150390625

In [ ]:
def prepare_dataset(batch):
    # load and resample audio data from 48 to 16kHz
    audio = batch["audio"]

    # compute log-Mel input features from input audio array
    batch["input_features"] = feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]

    # encode target text to label ids
    batch["labels"] = tokenizer(batch["sentence"]).input_ids
    return batch

In [ ]:
common_voice = common_voice.map(prepare_dataset, remove_columns=common_voice.column_names["train"], num_proc=2)

## Training and Evaluation

### Load a Pre-Trained Checkpoint

In [ ]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-small")

config.json:   0%|          | 0.00/1.97k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/967M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/3.87k [00:00<?, ?B/s]

In [ ]:
model.generation_config.language = "sinhala"
model.generation_config.task = "transcribe"

model.generation_config.forced_decoder_ids = None

### Define a Data Collator

In [ ]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any
    decoder_start_token_id: int

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.decoder_start_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch

In [ ]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(
    processor=processor,
    decoder_start_token_id=model.config.decoder_start_token_id,
)

### Evaluation Metrics

In [ ]:
import evaluate

metric = evaluate.load("wer")

In [ ]:
def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}

In [ ]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    A token is already saved on your machine. Run `huggingface-cli whoami` to get more information or `huggingface-cli logout` if you want to log out.
    Setting a new token will erase the existing one.
    To log in, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) y
Token is valid (permission: write

### Define the Training Configuration

In [ ]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="./Lingalingeswaran/whisper-small-sinhala_v1",  # change to a repo name of your choice
    per_device_train_batch_size=16,
    gradient_accumulation_steps=1,  # increase by 2x for every 2x decrease in batch size
    learning_rate=1e-5,
    warmup_steps=500,
    max_steps=4000,
    gradient_checkpointing=True,
    fp16=True,
    evaluation_strategy="steps",
    per_device_eval_batch_size=8,
    predict_with_generate=True,
    generation_max_length=225,
    save_steps=1000,
    eval_steps=1000,
    logging_steps=25,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="wer",
    greater_is_better=False,
    push_to_hub=True,
)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1575: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [ ]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=common_voice["train"],
    eval_dataset=common_voice["test"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor,
)

In [ ]:
from transformers import Seq2SeqTrainer

# Assuming your dataset has a 'validation' split, use it for evaluation
trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=common_voice["train"],
    # eval_dataset=common_voice["validation"],  # Changed from 'test' to 'validation'
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor,
)

In [ ]:
processor.save_pretrained(training_args.output_dir)

[]

### Training

In [ ]:
trainer.train()

Passing a tuple of `past_key_values` is deprecated and will be removed in Transformers v4.43.0. You should pass an instance of `EncoderDecoderCache` instead, e.g. `past_key_values=EncoderDecoderCache.from_legacy_cache(past_key_values)`.
`use_cache = True` is incompatible with gradient checkpointing. Setting `use_cache = False`...
/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:295: FutureWarning: `torch.cpu.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cpu', args...)` instead.
  with torch.enable_grad(), device_autocast_ctx, torch.cpu.amp.autocast(**ctx.cpu_autocast_kwargs):  # type: ignore[attr-defined]


You have passed task=transcribe, but also have set `forced_decoder_ids` to [[1, 50259], [2, 50359], [3, 50363]] which creates a conflict. `forced_decoder_ids` will be ignored in favor of task=transcribe.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:2618: UserWarning: Moving the following attributes in the config to the generation config: {'max_length': 448, 'suppress_tokens': [1, 2, 7, 8, 9, 10, 14, 25, 26, 27, 28, 29, 31, 58, 59, 60, 61, 62, 63, 90, 91, 92, 93, 359, 503, 522, 542, 873, 893, 902, 918, 922, 931, 1350, 1853, 1982, 2460, 2627, 3246, 3253, 3268, 3536, 3846, 3961, 4183, 4667, 6585, 6647, 7273, 9061, 9383, 10428, 10929, 11938, 12033, 12331, 12562, 13793, 14157, 14635, 15265, 15618, 16553, 16604, 18362, 18956, 20075, 21675, 2

/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:295: FutureWarning: `torch.cpu.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cpu', args...)` instead.
  with torch.enable_grad(), device_autocast_ctx, torch.cpu.amp.autocast(**ctx.cpu_autocast_kwargs):  # type: ignore[attr-defined]
There were missing keys in the checkpoint model loaded: ['proj_out.weight'].


TrainOutput(global_step=4000, training_loss=0.15594993942976, metrics={'train_runtime': 41086.236, 'train_samples_per_second': 1.558, 'train_steps_per_second': 0.097, 'total_flos': 1.846831127887872e+19, 'train_loss': 0.15594993942976, 'epoch': 1.196888090963495})

Our best WER is 43.0% - not bad for 8h of training data! We can make our model more accessible on the Hub with appropriate tags and README information.
You can change these values to match your dataset, language and model
name accordingly:

In [ ]:
kwargs = {
    "dataset_tags": "mozilla-foundation/common_voice_11_0",
    "dataset": "Common Voice 11.0",  # a 'pretty' name for the training dataset
    "dataset_args": "config: ta, split: test",
    "language": "ta",
    "model_name": "Whisper Small ta - Lingalingeswaran",  # a 'pretty' name for our model
    "finetuned_from": "openai/whisper-small",
    "tasks": "automatic-speech-recognition",
}

In [ ]:
trainer.push_to_hub(**kwargs)

No files have been modified since last commit. Skipping to prevent empty commit.


CommitInfo(commit_url='https://huggingface.co/Lingalingeswaran/whisper-small-ta/commit/52b10142e1efd332211ac1456b32566350b69cc7', commit_message='End of training', commit_description='', oid='52b10142e1efd332211ac1456b32566350b69cc7', pr_url=None, repo_url=RepoUrl('https://huggingface.co/Lingalingeswaran/whisper-small-ta', endpoint='https://huggingface.co', repo_type='model', repo_id='Lingalingeswaran/whisper-small-ta'), pr_revision=None, pr_num=None)

## Building a Demo

In [ ]:
!pip install gradio
import gradio as gr
from transformers import pipeline

pipe = pipeline(model="Lingalingeswaran/whisper-small-ta")

def transcribe(audio):
    text = pipe(audio)["text"]
    return text

iface = gr.Interface(
    fn=transcribe,
    # The 'source' argument has been replaced with 'sources' and requires a list.
    # Since you want to record from microphone, use sources=["microphone"].
    inputs=gr.Audio(sources=["microphone"], type="filepath"),
    outputs="text",
    title="Whisper Small Tamil",
    description="Realtime demo for Tamil speech recognition using a fine-tuned Whisper small model.",
)

iface.launch()

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.2/57.2 MB 8.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 320.4/320.4 kB 6.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 94.8/94.8 kB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.2/11.2 MB 20.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.2/73.2 kB 3.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.3/62.3 kB 2.3 MB/s eta 0:00:00
  Attempting uninstall: markupsafe
    Found existing installation: MarkupSafe 3.0.2
    Uninstalling MarkupSafe-3.0.2:
      Successfully uninstalled MarkupSafe-3.0.2


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.38k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/967M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/3.79k [00:00<?, ?B/s]

...

normalizer.json:   0%|          | 0.00/52.7k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/34.6k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.19k [00:00<?, ?B/s]

preprocessor_config.json:   0%|          | 0.00/339 [00:00<?, ?B/s]

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://1c49acff1e748c3596.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


## Closing Remarks

In [ ]:
import gradio as gr
from transformers import pipeline

# Initialize the pipeline with the specified model
pipe = pipeline(model="Lingalingeswaran/whisper-small-ta")

def transcribe(audio):
    # Transcribe the audio file to text
    text = pipe(audio)["text"]
    return text

# Create the Gradio interface
# The 'source' argument has been replaced with 'sources' and requires a list.
# You can specify multiple sources like ["microphone", "upload"].
iface = gr.Interface(
    fn=transcribe,
    inputs=gr.Audio(sources=["microphone", "upload"], type="filepath"),
    outputs="text",
    title="Whisper Small Tamil",
    description="Realtime demo for Tamil speech recognition using a fine-tuned Whisper small model.",
)

# Launch the interface
if __name__ == "__main__":
    iface.launch()

Running Gradio in a Colab notebook requires sharing enabled. Automatically setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://44d1abd8fe70aaf864.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)
